In [1]:
from transformers import AutoTokenizer, AutoModelForSequenceClassification, DataCollatorWithPadding,BertTokenizer
from torch.utils.data import DataLoader
from torch.utils.data import Dataset, DataLoader, RandomSampler, SequentialSampler
BASE_MODEL = "bert-base-uncased"
LEARNING_RATE = 1e-5
MAX_LENGTH = 512
BATCH_SIZE = 32
EPOCHS = 20


# tokenizer = AutoTokenizer.from_pretrained(BASE_MODEL)
tokenizer =BertTokenizer.from_pretrained('bert-base-uncased')
model = AutoModelForSequenceClassification.from_pretrained(BASE_MODEL, num_labels=1)

2023-12-15 21:25:57.086709: I tensorflow/core/util/port.cc:113] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2023-12-15 21:25:57.118701: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2023-12-15 21:25:57.118732: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2023-12-15 21:25:57.119519: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2023-12-15 21:25:57.124581: I tensorflow/core/platform/cpu_feature_guar

In [2]:
for param in model.bert.parameters():
    param.requires_grad=False

In [3]:
import pandas as pd
import os
import torch
from transformers import AutoModelForMaskedLM
from transformers import AutoTokenizer
from transformers import DataCollatorForLanguageModeling
from tqdm import tqdm
# from datasets import Dataset
import warnings
import numpy as np
from sklearn.model_selection import train_test_split

df = pd.read_excel('./behaviour_simulation_train.xlsx', usecols=[1,2,3,4,5,6])
df.head()

date  likes  \
0  2020-12-12 00:47:00      1   
1  2018-06-30 10:04:20   2750   
2  2020-09-29 19:47:28     57   
3  2020-10-01 11:40:09    152   
4  2018-10-19 14:30:46     41   

                                             content        username  \
0  Spend your weekend morning with a Ham, Egg, an...    TimHortonsPH   
1  Watch rapper <mention> freestyle for over an H...       IndyMusic   
2  Canadian Armenian community demands ban on mil...       CBCCanada   
3  1st in Europe to be devastated by COVID-19, It...  MKWilliamsRome   
4  Congratulations to Pauletha Butts of <mention>...           BGISD   

                                               media inferred company  
0  [Photo(previewUrl='https://pbs.twimg.com/media...      tim hortons  
1  [Photo(previewUrl='https://pbs.twimg.com/media...      independent  
2  [Photo(previewUrl='https://pbs.twimg.com/media...              cbc  
3  [Photo(previewUrl='https://pbs.twimg.com/media...         williams  
4  [Photo(previewUrl='https://pbs.twimg.com/media...      independent

In [4]:
pd.set_option('display.max_colwidth', None)
df = df.drop(df.index[14518:14545])
# df.reset_index(drop=True)

In [5]:
df = df.reset_index(drop=True)

In [6]:
captions = pd.read_csv('./captions-cont.csv')
# captions2=pd.read_csv('./captions-cont.csv')
# combined_captions = pd.concat([captions, captions2], ignore_index=True)
# Replace empty or missing values with 'No information'
captions.fillna('No information', inplace=True)

In [7]:
captions

Captions
0                                            Picture of Tim Hortons
1                            Picture of the rapper is in the studio
2                               Picture of A soldier in afghanistan
3                 Picture of The beach in the town of sicily, italy
4       Picture of a student receiving a certificate from a teacher
...                                                             ...
27080                                                         a pug
27081                                             A man on a bridge
27082  a woman holding a piece of food and a set of plastic rockets
27083    The picture shows the president of nigeria, mr umaru umaru
27084                                   a police officer with a dog

[27085 rows x 1 columns]

In [8]:
df_new = pd.concat([df, captions], axis=1)

In [9]:
df_new.dropna(inplace=True)

In [10]:
df_new['text'] = (
    "Input: \n"
    "The image of a tweet has the following information:\n" +
    df_new['Captions'] + "\n" +
    "...\n"+
    "It was posted by " + df_new['username'] + " on Twitter with the content '" +
    df_new['content'] + "' on " + df_new['date'] + ". The inferred company based on the tweet was " +
    df_new['inferred company'] + " company.  Predict the amount of likes that the tweet got anywhere from \"0\" to \"2000\", based on the date, content, image description, username, and inferred company. Use historical data and relevant events to enhance the predictive capabilities. For instance, leverage known trends, popular topics, or significant events that occurred on specific dates to enrich understanding and prediction accuracy. It is imperative that you only reply by the number of likes. And also vary the likes."
)


In [11]:
columns_to_drop = ['date', 'username', 'inferred company', 'Captions','media','content']
df_new.drop(columns=columns_to_drop, inplace=True)
df_new

likes  \
0          1   
1       2750   
2         57   
3        152   
4         41   
...      ...   
27080      0   
27081      2   
27082     51   
27083      0   
27084    190   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              text  
0                                                              Input: \nThe image of a tweet has the following information:\nPicture of Tim Hortons\n...\nIt was posted by TimHortonsPH on Twitter with the content 'Spend your weekend morning with a Ham, Egg, and Cheese Wrap paired with a sweet Iced French Vanilla! ☀️ Order yours now via dine-in, takeout, and delivery. #TimHortonsPH <hyperlink>' on 2020-12-12 00:47:00. The inferred company based on the tweet was tim hortons company.  Predict the amount of likes that the tweet got anywhere from "0" to "2000", based on the date, content, image description, username, and inferred company. Use historical data and relevant events to enhance the predictive capabilities. For instance, leverage known trends, popular topics, or significant events that occurred on specific dates to enrich understanding and prediction accuracy. It is imperative that you only reply by the number of likes. And also vary the likes.  
1                                                                                                                                                             Input: \nThe image of a tweet has the following information:\nPicture of the rapper is in the studio\n...\nIt was posted by IndyMusic on Twitter with the content 'Watch rapper <mention> freestyle for over an HOUR <hyperlink> <hyperlink>' on 2018-06-30 10:04:20. The inferred company based on the tweet was independent company.  Predict the amount of likes that the tweet got anywhere from "0" to "2000", based on the date, content, image description, username, and inferred company. Use historical data and relevant events to enhance the predictive capabilities. For instance, leverage known trends, popular topics, or significant events that occurred on specific dates to enrich understanding and prediction accuracy. It is imperative that you only reply by the number of likes. And also vary the likes.  
2                                                                                                                                         Input: \nThe image of a tweet has the following information:\nPicture of A soldier in afghanistan\n...\nIt was posted by CBCCanada on Twitter with the content 'Canadian Armenian community demands ban on military drone tech exports to Turkey <hyperlink> <hyperlink>' on 2020-09-29 19:47:28. The inferred company based on the tweet was cbc company.  Predict the amount of likes that the tweet got anywhere from "0" to "2000", based on the date, content, image description, username, and inferred company. Use historical data and relevant events to enhance the predictive capabilities. For instance, leverage known trends, popular topics, or significant events that occurred on specific dates to enrich understanding and prediction accuracy. It is imperative that you only reply by th

In [12]:
df_new.reset_index(drop=True, inplace=True)

In [13]:
from sklearn.preprocessing import StandardScaler
scaled_likes = df_new['likes']

# Reshape the column to a 2D array (required by StandardScaler)
scaled_likes = scaled_likes.values.reshape(-1, 1)

# Instantiate the StandardScaler
scaler = StandardScaler()

# Fit the scaler to your data and transform the column
scaled_column = scaler.fit_transform(scaled_likes)

# Include the scaled values back into your DataFrame
df_new['scaled_likes'] = scaled_column

In [14]:
selected_columns = ["text","scaled_likes"]
df_scaled=df_new[selected_columns].copy()

In [15]:
df_scaled

text  \
0                                                              Input: \nThe image of a tweet has the following information:\nPicture of Tim Hortons\n...\nIt was posted by TimHortonsPH on Twitter with the content 'Spend your weekend morning with a Ham, Egg, and Cheese Wrap paired with a sweet Iced French Vanilla! ☀️ Order yours now via dine-in, takeout, and delivery. #TimHortonsPH <hyperlink>' on 2020-12-12 00:47:00. The inferred company based on the tweet was tim hortons company.  Predict the amount of likes that the tweet got anywhere from "0" to "2000", based on the date, content, image description, username, and inferred company. Use historical data and relevant events to enhance the predictive capabilities. For instance, leverage known trends, popular topics, or significant events that occurred on specific dates to enrich understanding and prediction accuracy. It is imperative that you only reply by the number of likes. And also vary the likes.   
1                                                                                                                                                             Input: \nThe image of a tweet has the following information:\nPicture of the rapper is in the studio\n...\nIt was posted by IndyMusic on Twitter with the content 'Watch rapper <mention> freestyle for over an HOUR <hyperlink> <hyperlink>' on 2018-06-30 10:04:20. The inferred company based on the tweet was independent company.  Predict the amount of likes that the tweet got anywhere from "0" to "2000", based on the date, content, image description, username, and inferred company. Use historical data and relevant events to enhance the predictive capabilities. For instance, leverage known trends, popular topics, or significant events that occurred on specific dates to enrich understanding and prediction accuracy. It is imperative that you only reply by the number of likes. And also vary the likes.   
2                                                                                                                                         Input: \nThe image of a tweet has the following information:\nPicture of A soldier in afghanistan\n...\nIt was posted by CBCCanada on Twitter with the content 'Canadian Armenian community demands ban on military drone tech exports to Turkey <hyperlink> <hyperlink>' on 2020-09-29 19:47:28. The inferred company based on the tweet was cbc company.  Predict the amount of likes that the tweet got anywhere from "0" to "2000", based on the date, content, image description, username, and inferred company. Use historical data and relevant events to enhance the predictive capabilities. For instance, leverage known trends, popular topics, or significant events that occurred on specific dates to enrich understanding and prediction accuracy. It is imperative that you only reply by the number of likes. And also vary the likes.   
3                                                                            Input: \nThe image of a tweet has the following information:\nPicture of The beach in the town of sicily, italy\n...\nIt was posted by MKWilliamsRome on Twitter with the content '1st in Europe to be devastated by COVID-19, Italy redoubled its efforts, and they're now paying off. My latest. 👇🏼👇🏼\n<hyperlink> <hyperlink>' on 2020-10-01 11:40:09. The inferred company based on the tweet was williams company.  Predict the amount of likes that the tweet got anywhere from "0" to "2000", based on the date, content, image description, username, and inferred company. Use historical data and relevant events to enhance the predictive capabilities. For instance, leverage known trends, popular topics, or significant events that occurred on specific dates to enrich understanding and prediction accuracy. It is imperative that you only reply by the number of likes. And also vary the likes.   
4              Input: \nThe image of a tweet has the following information:\nPicture of a student receiving a certificate from a

In [16]:
from sklearn.model_selection import train_test_split
from datasets import Dataset

train_ratio = 0.7  # 70% train
val_ratio = 0.15   # 15% validation
test_ratio = 0.15   # 15% test

train_val, test = train_test_split(df_scaled, test_size=test_ratio, random_state=42)
train, val = train_test_split(train_val, test_size=val_ratio/(1-test_ratio), random_state=42)

# Converting the split data into Datasets
train_dataset = Dataset.from_pandas(train)
val_dataset = Dataset.from_pandas(val)
test_dataset = Dataset.from_pandas(test)

In [17]:
ds = {"train": train_dataset, "validation": val_dataset, "test": test_dataset}

def preprocess_function(examples):
    label = examples["scaled_likes"] 
    examples = tokenizer(examples["text"], truncation=True, padding="max_length", max_length=256,add_special_tokens=True,)
    
    # Change this to real number
    examples["label"] = float(label)
    return examples

for split in ds:
    ds[split] = ds[split].map(preprocess_function, remove_columns=["text", "scaled_likes", "__index_level_0__"])


Map:   0%|          | 0/18959 [00:00<?, ? examples/s]

Map:   0%|          | 0/4063 [00:00<?, ? examples/s]

Map:   0%|          | 0/4063 [00:00<?, ? examples/s]

In [18]:
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import mean_squared_error
from sklearn.metrics import r2_score

def compute_metrics_for_regression(eval_pred):
    logits, labels = eval_pred
    # labels = labels.reshape(-1)
    labels = labels.reshape(-1, 1)
    
    mse = mean_squared_error(y_true=labels, y_pred=logits)
    # mae = mean_absolute_error(labels, logits)
    rmse = mean_squared_error(y_true=labels, y_pred=logits, squared=False)
    # r2 = r2_score(labels, logits)
    # single_squared_errors = ((logits - labels).flatten()**2).tolist()
    
    # Compute accuracy 
    # Based on the fact that the rounded score = true score only if |single_squared_errors| < 0.5
    # accuracy = sum([1 for e in single_squared_errors if e < 0.25]) / len(single_squared_errors)
    max_logits = np.max(logits)  # Compute max value from logits
    
    # Log only scalar values for TensorBoard
    # scalar_metrics = {"mse": mse, "rmse": rmse, "max_logits": max_logits}
    
    # Return the scalar metrics along with the logits and labels for further analysis
    # return scalar_metrics, {'logits': logits, 'labels': labels}
    return {"mse": mse, "rmse": rmse,"labelshape":labels.shape, "logits":logits.shape}

In [19]:
from transformers import TrainingArguments, Trainer

training_args = TrainingArguments(
    output_dir="./bert_regression",
    learning_rate=LEARNING_RATE,
    per_device_train_batch_size=800,
    per_device_eval_batch_size=400,
    num_train_epochs=EPOCHS,
    evaluation_strategy="epoch",
    save_strategy="epoch",
    save_total_limit=2,
    metric_for_best_model="rmse",
    greater_is_better=False,
    lr_scheduler_type="linear",
    load_best_model_at_end=True,
    weight_decay=0.01,
)

In [20]:
class RegressionTrainer(Trainer):
    def compute_loss(self, model, inputs, return_outputs=False):
        labels = inputs.get("labels")
        outputs = model(**inputs)
        print(outputs.get("logits"))
        print("......................")
        print(labels)
        logits = outputs.get("logits")
        loss = torch.nn.functional.mse_loss(logits.squeeze(), labels)
        return (loss, outputs) if return_outputs else loss

In [21]:
trainer = RegressionTrainer(
    model=model,
    args=training_args,
    train_dataset=ds["train"],
    eval_dataset=ds["validation"],
    compute_metrics=compute_metrics_for_regression,
)

Detected kernel version 4.18.0, which is below the recommended minimum of 5.5.0; this can cause the process to hang. It is recommended to upgrade the kernel to the minimum version or higher.


In [22]:
trainer.train()

/opt/conda/lib/python3.10/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '


tensor([[-0.0512],
        [-0.1694],
        [-0.3112],
        ...,
        [ 0.0132],
        [-0.0980],
        [ 0.0052]], device='cuda:0', grad_fn=<GatherBackward>)
......................
tensor([-0.1832, -0.1694, -0.1834,  ..., -0.1060, -0.1030, -0.1470],
       device='cuda:0')


/tmp/ipykernel_1451722/3245083239.py:9: UserWarning: Using a target size (torch.Size([1600])) that is different to the input size (torch.Size([1600, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  loss = torch.nn.functional.mse_loss(logits, labels)


tensor([[-0.2219],
        [-0.1866],
        [ 0.0145],
        ...,
        [-0.1771],
        [-0.0627],
        [-0.0872]], device='cuda:0', grad_fn=<GatherBackward>)
......................
tensor([-0.1729,  0.0849, -0.1714,  ..., -0.1254, -0.0363, -0.0624],
       device='cuda:0')
tensor([[-0.1656],
        [-0.2810],
        [ 0.1247],
        ...,
        [ 0.1746],
        [-0.1740],
        [-0.2584]], device='cuda:0', grad_fn=<GatherBackward>)
......................
tensor([-0.1766, -0.1834, -0.1817,  ..., -0.1802, -0.1812, -0.0695],
       device='cuda:0')
tensor([[ 0.0137],
        [-0.0676],
        [-0.1149],
        ...,
        [ 0.0419],
        [-0.4033],
        [-0.0587]], device='cuda:0', grad_fn=<GatherBackward>)
......................
tensor([ 5.2814, -0.1556, -0.1709,  ...,  0.5589, -0.1822, -0.1239],
       device='cuda:0')
tensor([[-0.0829],
        [ 0.0671],
        [-0.1864],
        ...,
        [-0.2701],
        [-0.1174],
        [ 0.0893]], device='cud

/tmp/ipykernel_1451722/3245083239.py:9: UserWarning: Using a target size (torch.Size([1359])) that is different to the input size (torch.Size([1359, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  loss = torch.nn.functional.mse_loss(logits, labels)


...

tensor([[-3.3275e-02],
        [ 3.2841e-03],
        [-1.7765e-02],
        [-1.8954e-02],
        [-2.6316e-02],
        [-4.5682e-03],
        [-2.9625e-02],
        [-3.8075e-02],
        [-2.6613e-02],
        [-2.4187e-02],
        [-3.1128e-02],
        [-4.1587e-02],
        [-2.5514e-02],
        [-1.7081e-02],
        [-2.0956e-02],
        [-2.0410e-02],
        [ 1.5172e-02],
        [-2.7581e-02],
        [-3.6517e-02],
        [-2.9571e-02],
        [-2.2346e-02],
        [-3.2104e-02],
        [-2.5098e-02],
        [-6.6542e-03],
        [-1.8445e-02],
        [-2.1507e-02],
        [-3.7189e-03],
        [-8.5416e-03],
        [-3.1806e-02],
        [-2.2839e-02],
        [-3.6866e-02],
        [-1.2774e-02],
        [-4.7528e-02],
        [ 6.8529e-03],
        [-5.4324e-03],
        [-3.9576e-02],
        [-3.2324e-02],
        [ 1.3664e-02],
        [-7.7636e-03],
        [-4.4066e-02],
        [-1.2617e-02],
        [-1.6124e-02],
        [-1.4765e-02],
        [-3

/tmp/ipykernel_1451722/3245083239.py:9: UserWarning: Using a target size (torch.Size([800])) that is different to the input size (torch.Size([800, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  loss = torch.nn.functional.mse_loss(logits, labels)


tensor([[-3.0733e-02],
        [-3.4358e-02],
        [-2.7166e-02],
        [-2.6405e-02],
        [-2.5934e-02],
        [ 1.4032e-02],
        [-3.3720e-02],
        [-2.8792e-03],
        [ 1.0313e-02],
        [-3.6373e-02],
        [ 4.7837e-03],
        [-4.6174e-02],
        [-3.9826e-02],
        [ 2.1501e-02],
        [-2.5412e-02],
        [ 6.4846e-03],
        [-2.4746e-02],
        [-2.9576e-02],
        [ 1.8956e-02],
        [-5.1423e-02],
        [-8.7734e-04],
        [-8.0336e-03],
        [-1.8007e-02],
        [ 1.2088e-03],
        [-2.3819e-02],
        [-8.9416e-03],
        [-8.4162e-03],
        [-1.5452e-02],
        [ 1.0418e-02],
        [-1.2192e-02],
        [-2.0035e-02],
        [-1.3114e-02],
        [ 7.7932e-03],
        [-1.8284e-02],
        [-3.4264e-02],
        [ 3.9887e-03],
        [-7.6525e-03],
        [ 6.6023e-03],
        [-9.4120e-03],
        [-3.1309e-02],
        [ 4.8303e-03],
        [ 1.2807e-02],
        [-5.5839e-02],
        [-2

/tmp/ipykernel_1451722/3245083239.py:9: UserWarning: Using a target size (torch.Size([63])) that is different to the input size (torch.Size([63, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  loss = torch.nn.functional.mse_loss(logits, labels)
Trainer is attempting to log a value of "(4063, 1)" of type <class 'tuple'> for key "eval/labelshape" as a scalar. This invocation of Tensorboard's writer.add_scalar() is incorrect so we dropped this attribute.
Trainer is attempting to log a value of "(4063, 1)" of type <class 'tuple'> for key "eval/logits" as a scalar. This invocation of Tensorboard's writer.add_scalar() is incorrect so we dropped this attribute.


TrainOutput(global_step=240, training_loss=0.9669889450073242, metrics={'train_runtime': 1527.9323, 'train_samples_per_second': 248.165, 'train_steps_per_second': 0.157, 'total_flos': 4.988277710435328e+16, 'train_loss': 0.9669889450073242, 'epoch': 20.0})

In [23]:
trainer.eval_dataset=ds["test"]
trainer.evaluate()

/opt/conda/lib/python3.10/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '


tensor([[-0.0132],
        [-0.0173],
        [-0.0325],
        [ 0.0355],
        [-0.0368],
        [-0.0301],
        [-0.0071],
        [-0.0396],
        [-0.0262],
        [-0.0177],
        [ 0.0243],
        [-0.0385],
        [-0.0174],
        [-0.0444],
        [-0.0197],
        [ 0.0043],
        [-0.0139],
        [-0.0087],
        [-0.0134],
        [-0.0568],
        [-0.0112],
        [-0.0113],
        [-0.0035],
        [-0.0088],
        [-0.0191],
        [-0.0325],
        [-0.0170],
        [ 0.0031],
        [ 0.0229],
        [-0.0068],
        [-0.0247],
        [-0.0255],
        [ 0.0236],
        [-0.0527],
        [-0.0595],
        [ 0.0230],
        [ 0.0121],
        [ 0.0157],
        [-0.0034],
        [-0.0013],
        [-0.0153],
        [-0.0037],
        [-0.0081],
        [-0.0005],
        [-0.0033],
        [-0.0194],
        [-0.0283],
        [ 0.0429],
        [-0.0426],
        [-0.0349],
        [-0.0159],
        [-0.0032],
        [-0.

/tmp/ipykernel_1451722/3245083239.py:9: UserWarning: Using a target size (torch.Size([800])) that is different to the input size (torch.Size([800, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  loss = torch.nn.functional.mse_loss(logits, labels)


tensor([[-0.0048],
        [-0.0436],
        [-0.0027],
        [-0.0087],
        [-0.0283],
        [-0.0435],
        [-0.0097],
        [-0.0422],
        [ 0.0458],
        [-0.0061],
        [-0.0334],
        [-0.0432],
        [-0.0002],
        [-0.0273],
        [ 0.0158],
        [-0.0054],
        [ 0.0067],
        [-0.0362],
        [-0.0245],
        [-0.0228],
        [ 0.0160],
        [-0.0278],
        [-0.0483],
        [-0.0115],
        [-0.0330],
        [-0.0005],
        [-0.0279],
        [-0.0198],
        [-0.0235],
        [ 0.0050],
        [-0.0046],
        [-0.0069],
        [-0.0008],
        [ 0.0131],
        [ 0.0027],
        [-0.0272],
        [-0.0120],
        [-0.0192],
        [-0.0370],
        [ 0.0059],
        [-0.0249],
        [-0.0053],
        [-0.0085],
        [ 0.0130],
        [-0.0109],
        [ 0.0205],
        [-0.0136],
        [-0.0061],
        [-0.0492],
        [-0.0093],
        [-0.0227],
        [-0.0010],
        [-0.

/tmp/ipykernel_1451722/3245083239.py:9: UserWarning: Using a target size (torch.Size([63])) that is different to the input size (torch.Size([63, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  loss = torch.nn.functional.mse_loss(logits, labels)
Trainer is attempting to log a value of "(4063, 1)" of type <class 'tuple'> for key "eval/labelshape" as a scalar. This invocation of Tensorboard's writer.add_scalar() is incorrect so we dropped this attribute.
Trainer is attempting to log a value of "(4063, 1)" of type <class 'tuple'> for key "eval/logits" as a scalar. This invocation of Tensorboard's writer.add_scalar() is incorrect so we dropped this attribute.


{'eval_loss': 0.4921063780784607,
 'eval_mse': 0.4918922781944275,
 'eval_rmse': 0.7013503313064575,
 'eval_labelshape': (4063, 1),
 'eval_logits': (4063, 1),
 'eval_runtime': 13.1206,
 'eval_samples_per_second': 309.665,
 'eval_steps_per_second': 0.457,
 'epoch': 20.0}

In [24]:
model_directory = "./bert-trained2"  # Directory to save the model

# Save the trained model and tokenizer
model.save_pretrained(model_directory)  # Save the model weights and configuration
tokenizer.save_pretrained(model_directory)

('./bert-trained2/tokenizer_config.json',
 './bert-trained2/special_tokens_map.json',
 './bert-trained2/vocab.txt',
 './bert-trained2/added_tokens.json')

# Prediction on data


In [75]:
df_result1=pd.read_excel('./behaviour_simulation_test_company.xlsx')
df_result1

id                 date  \
0         1  2019-01-08 18:03:10   
1         2  2018-01-29 10:51:17   
2         3  2019-09-05 07:25:14   
3         4  2018-03-28 18:15:00   
4         5  2019-09-11 21:15:44   
...     ...                  ...   
9995   9996  2020-01-25 01:45:07   
9996   9997  2019-06-26 12:51:27   
9997   9998  2019-05-06 10:37:03   
9998   9999  2019-05-19 12:00:51   
9999  10000  2019-05-18 17:04:14   

                                                                                                                                                                                                                                                                                       content  \
0                                                                                                                                                                                                                                                     the Heathrow drone right now <hyperlink>   
1                                                                                                                                                                    A deal at £60m?\n\nThe latest on Pierre-Emerick Aubameyang with Arsenal closing in on a transfer: <hyperlink> <hyperlink>   
2                                                      "Dealing with Boris Johnson is like someone dealing with a two or three year old having a tantrum," says shadow chancellor John McDonnell, "this is about putting the country before party interest"\n\n<hyperlink> #Brexit <hyperlink>   
3                                                                                                                             Doesn't unlimited food &amp; drinks all night at #TellMeYouLoveMeTour sound pretty good?\n\nUpgrade your 🎟️ to <mention> and it's yours! <hyperlink> <hyperlink>   
4                                                                                                                                                          Apple Watch Series 5.\n\nYou’ve never seen a watch like this. This watch tells time. (Among other things.)  <hyperlink> <hyperlink>   
...                                                                                                                                                                                                                                                                                        ...   
9995  "So what do all these defenses mean? What they mean is: 'Under Article II, the President can do whatever he wants.' ... They want us to believe the President can do whatever he wants under Article II, and there is nothing you or the House can do about it." - <mention> <hyperlink>   
9996                                                                      In this week’s #MacroMemo, we explore last week’s Fed decision and what’s likely to come next. We also look at central bank decisions around the world, growing Iran-U.S. tensions and more: <hyperlink> <hyperlink>   
9997                                                                                                                                                                                                 When it's bank holiday Monday and someone mentions work tomorrow. #EastEnders <hyperlink>   
9998                                                                                                                            England boss Gareth Southgate says he is concerned by a "slide" in the number of English players starting <mention> games.\n\nIn full: <hyperlink> <hyperlink>   
9999                                                                                                                                                         We're back under way in the Women's Champions League final.\n\nLyon lead Barcelona 4-0.\n\nLIVE: <hyperlink>\n\n#WUCL <hyperlink>   

            username  \
0           bbcthree   
1           BBCSport   
2        BBCPolitics   

In [76]:
df_result1 = df_result1.reset_index(drop=True)

In [77]:
df_result1.dropna(inplace=True)

In [78]:
df_result1['text'] = (
    "Input: \n"
    "Tweet was posted by " + df_result1['username'] + " on Twitter with the content '" +
    df_result1['content'] + "' on " + df_result1['date'] + ". The inferred company based on the tweet was " +
    df_result1['inferred company'] + " company.  Predict the amount of likes that the tweet got anywhere from \"0\" to \"2000\", based on the date, content, image description, username, and inferred company. Use historical data and relevant events to enhance the predictive capabilities. For instance, leverage known trends, popular topics, or significant events that occurred on specific dates to enrich understanding and prediction accuracy. It is imperative that you only reply by the number of likes. And also vary the likes."
)
df_result1

id                 date  \
0         1  2019-01-08 18:03:10   
1         2  2018-01-29 10:51:17   
2         3  2019-09-05 07:25:14   
3         4  2018-03-28 18:15:00   
4         5  2019-09-11 21:15:44   
...     ...                  ...   
9995   9996  2020-01-25 01:45:07   
9996   9997  2019-06-26 12:51:27   
9997   9998  2019-05-06 10:37:03   
9998   9999  2019-05-19 12:00:51   
9999  10000  2019-05-18 17:04:14   

                                                                                                                                                                                                                                                                                       content  \
0                                                                                                                                                                                                                                                     the Heathrow drone right now <hyperlink>   
1                                                                                                                                                                    A deal at £60m?\n\nThe latest on Pierre-Emerick Aubameyang with Arsenal closing in on a transfer: <hyperlink> <hyperlink>   
2                                                      "Dealing with Boris Johnson is like someone dealing with a two or three year old having a tantrum," says shadow chancellor John McDonnell, "this is about putting the country before party interest"\n\n<hyperlink> #Brexit <hyperlink>   
3                                                                                                                             Doesn't unlimited food &amp; drinks all night at #TellMeYouLoveMeTour sound pretty good?\n\nUpgrade your 🎟️ to <mention> and it's yours! <hyperlink> <hyperlink>   
4                                                                                                                                                          Apple Watch Series 5.\n\nYou’ve never seen a watch like this. This watch tells time. (Among other things.)  <hyperlink> <hyperlink>   
...                                                                                                                                                                                                                                                                                        ...   
9995  "So what do all these defenses mean? What they mean is: 'Under Article II, the President can do whatever he wants.' ... They want us to believe the President can do whatever he wants under Article II, and there is nothing you or the House can do about it." - <mention> <hyperlink>   
9996                                                                      In this week’s #MacroMemo, we explore last week’s Fed decision and what’s likely to come next. We also look at central bank decisions around the world, growing Iran-U.S. tensions and more: <hyperlink> <hyperlink>   
9997                                                                                                                                                                                                 When it's bank holiday Monday and someone mentions work tomorrow. #EastEnders <hyperlink>   
9998                                                                                                                            England boss Gareth Southgate says he is concerned by a "slide" in the number of English players starting <mention> games.\n\nIn full: <hyperlink> <hyperlink>   
9999                                                                                                                                                         We're back under way in the Women's Champions League final.\n\nLyon lead Barcelona 4-0.\n\nLIVE: <hyperlink>\n\n#WUCL <hyperlink>   

            username  \
0           bbcthree   
1           BBCSport   
2        BBCPolitics   

In [79]:
columns_to_drop = ['id', 'username', 'inferred company','media','content','date']
df_result1.drop(columns=columns_to_drop, inplace=True)
df_result1

text
0                                                                                                                                                                                                                                                             Input: \nTweet was posted by bbcthree on Twitter with the content 'the Heathrow drone right now <hyperlink>' on 2019-01-08 18:03:10. The inferred company based on the tweet was bbc company.  Predict the amount of likes that the tweet got anywhere from "0" to "2000", based on the date, content, image description, username, and inferred company. Use historical data and relevant events to enhance the predictive capabilities. For instance, leverage known trends, popular topics, or significant events that occurred on specific dates to enrich understanding and prediction accuracy. It is imperative that you only reply by the number of likes. And also vary the likes.
1                                                                                                                                                                            Input: \nTweet was posted by BBCSport on Twitter with the content 'A deal at £60m?\n\nThe latest on Pierre-Emerick Aubameyang with Arsenal closing in on a transfer: <hyperlink> <hyperlink>' on 2018-01-29 10:51:17. The inferred company based on the tweet was bbc company.  Predict the amount of likes that the tweet got anywhere from "0" to "2000", based on the date, content, image description, username, and inferred company. Use historical data and relevant events to enhance the predictive capabilities. For instance, leverage known trends, popular topics, or significant events that occurred on specific dates to enrich understanding and prediction accuracy. It is imperative that you only reply by the number of likes. And also vary the likes.
2                                                           Input: \nTweet was posted by BBCPolitics on Twitter with the content '"Dealing with Boris Johnson is like someone dealing with a two or three year old having a tantrum," says shadow chancellor John McDonnell, "this is about putting the country before party interest"\n\n<hyperlink> #Brexit <hyperlink>' on 2019-09-05 07:25:14. The inferred company based on the tweet was bbc company.  Predict the amount of likes that the tweet got anywhere from "0" to "2000", based on the date, content, image description, username, and inferred company. Use historical data and relevant events to enhance the predictive capabilities. For instance, leverage known trends, popular topics, or significant events that occurred on specific dates to enrich understanding and prediction accuracy. It is imperative that you only reply by the number of likes. And also vary the likes.
3                                                                                                                       Input: \nTweet was posted by BrdgstoneArena on Twitter with the content 'Doesn't unlimited food &amp; drinks all night at #TellMeYouLoveMeTour sound pretty good?\n\nUpgrade your 🎟️ to <mention> and it's yours! <hyperlink> <hyperlink>' on 2018-03-28 18:15:00. The inferred company based on the tweet was bridgestone company.  Predict the amount of likes that the tweet got anywhere from "0" to "2000", based on the date, content, image description, username, and inferred company. Use historical data and relevant events to enhance the predictive capabilities. For instance, leverage known trends, popular topics, or significant events that occurred on specific dates to enrich understanding and prediction accuracy. It is imperative that you only reply by the number of likes. And also vary the likes.
4                                                                                                                                                              Input: \nTweet was posted by BestBuy on Twitter with the content 'Apple Watch Series 5.\n\nYou’ve never seen a watch like this. This watch tells tim

In [80]:
result_dataset= Dataset.from_pandas(df_result1)

In [81]:
import math
import pandas as pd
import torch
# Convert the Dataset to a Pandas DataFrame

nb_batches = math.ceil(len(result_dataset)/200)
y_preds = []

for i in range(nb_batches):
    input_texts = result_dataset[i * 200: (i+1) * 200]["text"]
    # input_labels = result_dataset[i * 200: (i+1) * BATCH_SIZE]["scaled_likes"]
    encoded = tokenizer(input_texts, truncation=True, padding="max_length", max_length=256, add_special_tokens=True)
    input_ids = torch.tensor(encoded['input_ids']).to('cuda:0') # Convert input_ids to a tensor
    attention_mask = torch.tensor(encoded['attention_mask']).to('cuda:0') # Assuming the tokenizer returns attention_mask
    
    batch_y_preds = model(input_ids, attention_mask=attention_mask).logits
    
    # Append predictions for the current batch to y_preds list
    y_preds += batch_y_preds.detach().cpu().tolist()  
    # encoded = tokenizer(input_texts, truncation=True, padding="max_length", max_length=256,add_special_tokens=True)
    # y_preds = model(**encoded).logits

# pd.set_option('display.max_rows', 500)
# test_df["likes"] = test_df["scaled_likes"] * (max_likes - min_likes) + min_likes
# df_out = pd.DataFrame([test_dataset["text"], test_df["likes"], y_preds_rescaled], ["Text", "likes", "Prediction"])

In [82]:
y_preds

[[-0.043104395270347595],
 [-0.024238690733909607],
 [-0.04766654968261719],
 [-0.03810597211122513],
 [0.0171564519405365],
 [-0.04722386598587036],
 [-0.02182023972272873],
 [0.009559824131429195],
 [-0.05182495713233948],
 [-0.04524989426136017],
 [-0.00024450637283734977],
 [-0.031956762075424194],
 [-0.01659846305847168],
 [-0.0327247753739357],
 [-0.030325450003147125],
 [-0.0562157928943634],
 [-0.03480539470911026],
 [-0.03751389682292938],
 [-0.03250254690647125],
 [-0.030636563897132874],
 [-0.04063453525304794],
 [-0.025935694575309753],
 [0.005578845273703337],
 [-0.0066224937327206135],
 [-0.0207316055893898],
 [-0.047529272735118866],
 [-0.036799147725105286],
 [-0.01808808743953705],
 [-0.028858281672000885],
 [-0.008970589376986027],
 [-0.0329003632068634],
 [-0.005785525310784578],
 [-0.015528515912592411],
 [-0.023044660687446594],
 [-0.008370147086679935],
 [-0.0167529433965683],
 [-0.003967583645135164],
 [-0.03366099298000336],
 [-0.008732722140848637],
 [0.0302066

In [83]:
y_preds_np = np.array(y_preds).reshape(-1, 1) 

In [84]:
y_preds_np

array([[-0.0431044 ],
       [-0.02423869],
       [-0.04766655],
       ...,
       [-0.06509031],
       [-0.03530386],
       [-0.03483088]])

In [85]:
y_preds_original_scale = scaler.inverse_transform(y_preds_np)

In [86]:
y_preds_original_scale

array([[570.50629012],
       [647.20055946],
       [551.9598797 ],
       ...,
       [481.12749511],
       [602.2176043 ],
       [604.14041905]])

In [87]:
y_preds_int = np.round(y_preds_original_scale).astype(int)

In [88]:
y_preds_int

array([[571],
       [647],
       [552],
       ...,
       [481],
       [602],
       [604]])

In [89]:
np.savetxt('behavior_test_company_results.csv', y_preds_int, delimiter=',', fmt='%d')